In [1]:
%pip install gensim

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Note: you may need to restart the kernel to use updated packages.


In [2]:
%pip install scipy==1.10.1

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
Note: you may need to restart the kernel to use updated packages.


In [3]:
import pandas as pd
import re
import nltk
from nltk.corpus import stopwords
from string import punctuation
nltk.download('wordnet')
from nltk.stem import WordNetLemmatizer
from nltk import sent_tokenize
import gensim
from gensim.models import Word2Vec
import warnings
warnings.filterwarnings('ignore')

[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/gigimancinelli./nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [4]:
translator = str.maketrans('','',punctuation) 
nltk.download('stopwords')
nltk.download('punkt')
stoplist = set(stopwords.words('english'))
lemmatizer = WordNetLemmatizer()


[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/gigimancinelli./nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/gigimancinelli./nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [5]:
df = pd.read_csv("./data/preprocessed_data_mpv.csv")

In [6]:
for i, row in df.iterrows():
    print(row.TextColumn)
    if i == 50:
        break

  a godfrey man who had been charged with murder in the shooting death of a woman inside a truck in missouri died thursday during a standoff with police in west alton  missouri  amy lynn delacruz  XXXXXX  of cadet  missouri  was identified as the victim found in the truck  according to cpl  barry bayles of the st  charles county  missouri  police department  her body was found early thursday in a tractor trailer in floristell  missouri  according to court records  clyde e  young  XXXXXX  of godfrey  died during a standoff with police at a gas station on u s  XXXXXX in west alton  missouri  near the clark bridge over the mississippi river  police said  bayles said investigators were trying to determine whether young was shot by police or if he died from a self inflicted gunshot  young had called XXXXXXXXX to say his girlfriend was shot in the truck in floristell  according to a probable cause statement filed in st  charles county court by the st  charles police department  young was not

In [7]:
df['TextColumn'] = df['TextColumn'].astype(str)

In [8]:
def remove_unwanted_content(text):
    patterns = [
        r'example video title will go here for this video',
        r'example video title',
        r'will go here for this video',
        r'this video',
        r'click here', 
        r'org',
        r'newsletter',
        r'latest local breaking news',
        r'breaking news', 
        r'news app',
        r'get today',
        r'apple',
        r'google',
        r'play store',
        r'app',
        r'streaming device',
        r'stream live',
        r'live video',
        r'news and updates',
        r'download',
        r'channel',
        r'searching',
        r'youtube',
        r'on demand videos',
        r'here watch',
        r'newscasts',
        r'content', 
        r'anytime',
        r'anywhere',
        r'once a day',
        r'free',
        r'you can now watch',
        r'your phone',
        r'up to speed',
        r'catch up on the latest news and stories',
        r'catch up',
        r'latest news',
        r'latest stories',
        r'review journal',
        r'digital content',
        r'news live',
        r'news',
        r'live',
        r'sign up for our newsletter',
        r'all rights reserved',
        r'check back for updates',
        r'email notifications',
        r'what s your reaction',
        r'your reaction',
        r'facebook',
        r'email',
        r'pic',
        r'chat',
        r'contributed to this report',
        r'this report',
        r'com',
        r'news bulletin press time',
        r'editor s note',
        r'this article was updated on',
        r'twitter',
        r'media group',
        r'stream channel',
        r'report a spelling or grammar error',
        r'please include the headline',
        r'copyright',
        r'smart tv apps',
        r'download our free news',
        r'daily',
        r'headline',
        r'there was a problem',
        r'saving your notification',
        r'your notification has been saved',
        r'saving your notification',
        r'description',
        r'email notifications are only sent once a day',
        r'email notifications',
        r'matching items',
        r'XXXXXX',
        r'XXX',
        r'notifications',
        r'watch'
        
    ]
    for pattern in patterns:
        text = re.sub(pattern, '', text)
    text = re.sub(r'\b[a-zA-Z]\b', '', text)
    text = re.sub(r'\s+', ' ', text).strip()
    return text

In [9]:
df['cleaned'] = df['TextColumn'].apply(remove_unwanted_content)

In [10]:
for i, row in df.iterrows():
    print(row.cleaned)
    if i == 50:
        break

godfrey man who had been charged with murder in the shooting death of woman inside truck in missouri died thursday during standoff with police in west alton missouri amy lynn delacruz of cadet missouri was identified as the victim found in the truck according to cpl barry bayles of the st charles county missouri police department her body was found early thursday in tractor trailer in floristell missouri according to court records clyde young of godfrey died during standoff with police at gas station on in west alton missouri near the clark bridge over the mississippi river police said bayles said investigators were trying to determine whether young was shot by police or if he died from self inflicted gunshot young had called to say his girlfriend was shot in the truck in floristell according to probable cause statement filed in st charles county court by the st charles police department young was not at the truck when police arrived but he later called an officer to say that he fired 

In [11]:
stop_words = set(stopwords.words('english'))

In [12]:
stop_words

{'a',
 'about',
 'above',
 'after',
 'again',
 'against',
 'ain',
 'all',
 'am',
 'an',
 'and',
 'any',
 'are',
 'aren',
 "aren't",
 'as',
 'at',
 'be',
 'because',
 'been',
 'before',
 'being',
 'below',
 'between',
 'both',
 'but',
 'by',
 'can',
 'couldn',
 "couldn't",
 'd',
 'did',
 'didn',
 "didn't",
 'do',
 'does',
 'doesn',
 "doesn't",
 'doing',
 'don',
 "don't",
 'down',
 'during',
 'each',
 'few',
 'for',
 'from',
 'further',
 'had',
 'hadn',
 "hadn't",
 'has',
 'hasn',
 "hasn't",
 'have',
 'haven',
 "haven't",
 'having',
 'he',
 'her',
 'here',
 'hers',
 'herself',
 'him',
 'himself',
 'his',
 'how',
 'i',
 'if',
 'in',
 'into',
 'is',
 'isn',
 "isn't",
 'it',
 "it's",
 'its',
 'itself',
 'just',
 'll',
 'm',
 'ma',
 'me',
 'mightn',
 "mightn't",
 'more',
 'most',
 'mustn',
 "mustn't",
 'my',
 'myself',
 'needn',
 "needn't",
 'no',
 'nor',
 'not',
 'now',
 'o',
 'of',
 'off',
 'on',
 'once',
 'only',
 'or',
 'other',
 'our',
 'ours',
 'ourselves',
 'out',
 'over',
 'own',
 'r

In [13]:
def normalize_text(doc):
    doc = doc.replace('\r', ' ').replace('\n', ' ')
    words = doc.split() 
    nostop = [w for w in words if w not in stop_words] 
    lemmas = [lemmatizer.lemmatize(w) for w in nostop] 
    return lemmas
  
def get_sentences(doc):
    sent=[]
    for raw in sent_tokenize(doc):
        raw2 = normalize_text(raw)
        sent.append(raw2)
    return sent

In [14]:
df['sentences'] = df['cleaned'].apply(get_sentences)

In [15]:
for i, row in df.iterrows():
    print(row.sentences)
    if i == 50:
        break

[['godfrey', 'man', 'charged', 'murder', 'shooting', 'death', 'woman', 'inside', 'truck', 'missouri', 'died', 'thursday', 'standoff', 'police', 'west', 'alton', 'missouri', 'amy', 'lynn', 'delacruz', 'cadet', 'missouri', 'identified', 'victim', 'found', 'truck', 'according', 'cpl', 'barry', 'bayles', 'st', 'charles', 'county', 'missouri', 'police', 'department', 'body', 'found', 'early', 'thursday', 'tractor', 'trailer', 'floristell', 'missouri', 'according', 'court', 'record', 'clyde', 'young', 'godfrey', 'died', 'standoff', 'police', 'gas', 'station', 'west', 'alton', 'missouri', 'near', 'clark', 'bridge', 'mississippi', 'river', 'police', 'said', 'bayles', 'said', 'investigator', 'trying', 'determine', 'whether', 'young', 'shot', 'police', 'died', 'self', 'inflicted', 'gunshot', 'young', 'called', 'say', 'girlfriend', 'shot', 'truck', 'floristell', 'according', 'probable', 'cause', 'statement', 'filed', 'st', 'charles', 'county', 'court', 'st', 'charles', 'police', 'department', 'yo

In [16]:
sentences = []
for i, row in df.iterrows():
    sentence = row.sentences
    for sent in sentence:
        sentences.append(sent)

In [17]:
sentences

[['godfrey',
  'man',
  'charged',
  'murder',
  'shooting',
  'death',
  'woman',
  'inside',
  'truck',
  'missouri',
  'died',
  'thursday',
  'standoff',
  'police',
  'west',
  'alton',
  'missouri',
  'amy',
  'lynn',
  'delacruz',
  'cadet',
  'missouri',
  'identified',
  'victim',
  'found',
  'truck',
  'according',
  'cpl',
  'barry',
  'bayles',
  'st',
  'charles',
  'county',
  'missouri',
  'police',
  'department',
  'body',
  'found',
  'early',
  'thursday',
  'tractor',
  'trailer',
  'floristell',
  'missouri',
  'according',
  'court',
  'record',
  'clyde',
  'young',
  'godfrey',
  'died',
  'standoff',
  'police',
  'gas',
  'station',
  'west',
  'alton',
  'missouri',
  'near',
  'clark',
  'bridge',
  'mississippi',
  'river',
  'police',
  'said',
  'bayles',
  'said',
  'investigator',
  'trying',
  'determine',
  'whether',
  'young',
  'shot',
  'police',
  'died',
  'self',
  'inflicted',
  'gunshot',
  'young',
  'called',
  'say',
  'girlfriend',
  'sh

In [18]:
df.to_csv("data/mpv_clean_pattern_stop.csv")

## word2vec
We test different embedding dimensions and different witndow sizes to get the best vector representations. While it is hard to properly define a measure that helps us tune the hyperparameters, we evaluate based on classical similarities between words.

In [19]:
num_words_list = [100, 200, 300]
windows_val = [3, 5, 7]
models = {'dim': [], 'window': [], 'model': []}
for num_words in num_words_list:
    for wind in windows_val:
        model = Word2Vec (sentences, 
                          vector_size = num_words, 
                          min_count=1,
                          window=wind,
                          seed=42, 
                          workers=8)
        models['model'].append(model)
        models['dim'].append(num_words)
        models['window'].append(wind)

In [20]:
models

{'dim': [100, 100, 100, 200, 200, 200, 300, 300, 300],
 'window': [3, 5, 7, 3, 5, 7, 3, 5, 7],
 'model': [<gensim.models.word2vec.Word2Vec at 0x31dc9a190>,
  <gensim.models.word2vec.Word2Vec at 0x13f16db50>]}

In [21]:
query = 'man'
for i in range (len (models['model'])):
    model = models['model'][i]
    print (f"Model with vector dimension={models['dim'][i]} and window size={models['window'][i]}")
    for item in model.wv.most_similar(query, topn=5):
        print(item)
    print()

Model with vector dimension=100 and window size=3
('woman', 0.800227701663971)
('suspect', 0.7905324101448059)
('person', 0.7539744973182678)
('gunman', 0.6981064081192017)
('individual', 0.6663126349449158)

Model with vector dimension=100 and window size=5
('woman', 0.7744371891021729)
('suspect', 0.7637491822242737)
('person', 0.7422451376914978)
('gunman', 0.6163017153739929)
('someone', 0.5924066305160522)

Model with vector dimension=100 and window size=7
('woman', 0.7640409469604492)
('suspect', 0.7149462699890137)
('person', 0.6507073640823364)
('reportedly', 0.5650641322135925)
('someone', 0.5553724765777588)

Model with vector dimension=200 and window size=3
('suspect', 0.7450171113014221)
('person', 0.7083973288536072)
('woman', 0.7083067893981934)
('gunman', 0.6644523739814758)
('individual', 0.5857474207878113)

Model with vector dimension=200 and window size=5
('suspect', 0.6978077292442322)
('woman', 0.679885983467102)
('person', 0.6791579127311707)
('gunman', 0.57747042

#### Now we can extract the best model from the dictionary and save it. It will be the one used in our main analysis. The best model correspond to 100-dimensional vector with window size of 3.

In [22]:
model_ = models['model'][0]

In [23]:
model_.save("./model/word2vec.model")

In [38]:
for item in model_.wv.most_similar(positive= ['black', 'man'],  topn=5):
    print(item)

('woman', 0.6278790235519409)
('teen', 0.6218199729919434)
('white', 0.5870969891548157)
('gunman', 0.5832531452178955)
('teenager', 0.5754038691520691)


In [37]:
for item in model_.wv.most_similar(positive= ['man', 'white'],  topn=5):
    print(item)

('male', 0.6940954327583313)
('suspect', 0.6797606348991394)
('woman', 0.6750169992446899)
('driver', 0.641150176525116)
('teen', 0.6310592889785767)


### We repeat the same analysis to get embeddings for article before and after George Floyd (May 25, 2020). We will use the best hyperparameters obtained before but we will train two new word2vec models: one for articles related to events that occoured before George Floyd, and one for articles related to events occouring after George Floyd. 

In [24]:
df_before_floyd = df[df.after_Floyd == False]
df_after_floyd = df[df.after_Floyd == True]

In [25]:
sentences_before = []
for i, row in df_before_floyd.iterrows():
    sentence_b = row.sentences
    for sent in sentence_b:
        sentences_before.append(sent)

In [26]:
sentences_after = []
for i, row in df_after_floyd.iterrows():
    sentence_a = row.sentences
    for sent in sentence_a:
        sentences_after.append(sent)

In [27]:
model_before = Word2Vec (sentences_before, 
                          vector_size = 100, 
                          min_count=1,
                          window=3,
                          seed=42, 
                          workers=8)

In [28]:
print (f'Model before George Floyd')
for item in model_before.wv.most_similar(query, topn=5):
    print(item)

Model before George Floyd
('suspect', 0.7882161140441895)
('gunman', 0.7700906991958618)
('woman', 0.7691831588745117)
('person', 0.7058723568916321)
('teen', 0.6979813575744629)


In [50]:
for item in model_before.wv.most_similar( positive= 'criminal',  topn=10):
    print(item)

('misconduct', 0.7234194874763489)
('history', 0.7163107395172119)
('rehension', 0.7106736302375793)
('conduct', 0.7102456092834473)
('trespass', 0.7083299160003662)
('disciplinary', 0.7074049711227417)
('allegation', 0.702959418296814)
('extensive', 0.6932017803192139)
('peace', 0.6883774995803833)
('prosecution', 0.6856609582901001)


In [41]:
for item in model_before.wv.most_similar(positive= ['black', 'man'],  topn=10):
    print(item)

('teen', 0.7755133509635925)
('white', 0.7591754198074341)
('unarmed', 0.7399629354476929)
('motorist', 0.7364965677261353)
('male', 0.7284963726997375)
('gunman', 0.7280170917510986)
('robber', 0.7245677709579468)
('teenager', 0.7235698699951172)
('pair', 0.7039340138435364)
('developmentally', 0.6988174319267273)


In [46]:
for item in model_before.wv.most_similar(positive= ['white', 'man'],  topn=10):
    print(item)

('male', 0.8283479809761047)
('teen', 0.7836729884147644)
('gunman', 0.7766477465629578)
('motorist', 0.7719221711158752)
('female', 0.7609922885894775)
('robber', 0.7450807690620422)
('suspect', 0.7337373495101929)
('pair', 0.7315754294395447)
('teenager', 0.7288225293159485)
('unidentified', 0.7219744324684143)


In [29]:
model_after = Word2Vec (sentences_after, 
                          vector_size = 100, 
                          min_count=1,
                          window=3,
                          seed=42, 
                          workers=8)

In [30]:
print (f'Model after George Floyd')
for item in model_after.wv.most_similar(query, topn=5):
    print(item)

Model after George Floyd
('suspect', 0.780234158039093)
('woman', 0.7732114195823669)
('person', 0.7662348747253418)
('gunman', 0.743096113204956)
('individual', 0.6565850377082825)


In [43]:
for item in model_after.wv.most_similar(positive= ['black', 'man'],  topn=10):
    print(item)

('gunman', 0.6652922034263611)
('teen', 0.6433224081993103)
('unarmed', 0.5990114212036133)
('humphrey', 0.5790920853614807)
('woman', 0.5782382488250732)
('boy', 0.5711727738380432)
('robber', 0.568853497505188)
('stealing', 0.5591616630554199)
('white', 0.5572484135627747)
('teenager', 0.555633008480072)


In [45]:
for item in model_after.wv.most_similar(positive= ['white', 'man'],  topn=10):
    print(item)
    

('male', 0.7017746567726135)
('suspect', 0.677986741065979)
('driver', 0.6661751866340637)
('toon', 0.6567124724388123)
('woman', 0.652825117111206)
('gunman', 0.6406068801879883)
('teen', 0.6300837397575378)
('hubbard', 0.6187493801116943)
('briggs', 0.6175493597984314)
('female', 0.6118980646133423)


In [32]:
#get dimension of the embedding matrix
model_before.wv.vectors.shape

(33337, 100)

In [31]:
model_before.save("./model/word2vec_before_floyd.model")
model_after.save("./model/word2vec_after_floyd.model")